![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 12. <i>Key logging</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Badania nad komputerowym wspomaganiem tłumaczenia często prowadzone są przy użyciu metodologii testowania interfejsów użytkownika - UI/UX testing. Program typu CAT traktuje się wówczas jak każdy inny program komputerowy i przeprowadza testy wydajności i użyteczności.

Testy takie prowadzone są zawsze na użytkownikach końcowych, w tym przypadku - na tłumaczach. Podstawowym celem testów jest próba zaobserwowania faktycznego sposobu pracy tłumacza - które funkcje programu są przez niego wykorzystywane najczęściej, jakich innych narzędzi poza CAT-em używa on do swojej pracy, które funkcje programu działają zgodnie, a które niezgodnie z intuicją użytkownika oraz wiele innych czynników. Aby wszystkie te analizy były możliwe, konieczne jest zgromadzenie jak największej ilości danych dotyczących przebiegu testu.

Testy są przede wszystkim nagrywane. Nagrywany jest zarówno ekran komputera (screen capture), jak i sam użytkownik pracujący przy komputerze. To jednak nie wszystko - często stosuje się specjalne techniki eye-trackingu, które są w stanie określić, w który punk ekranu użytkownik aktualnie patrzy. Dane pozyskane w ten sposób używane są do analizy czasu znalezienia przez użytkownika potrzebnej mu funkcji oraz zidentyfikowania miejsc, gdzie tej funkcji poszukiwał. Można również wyznaczyć obszary ekranu, które często skupiają uwagę użytkownika. 

Dodatkowo stosuje się jeszcze jedną technikę, która jest szczególnie przydatna z punktu widzenia analizy procesu tłumaczenia. Wykonuje się pełny key logging, tj. zapisuje się każde uderzenie użytkownika w dowolny klawisz na klawiaturze wraz z precyzyjnym czasem tego uderzenia. Dane pozyskane w ten sposób pozwalają na przeprowadzenie szeregu interesujących analiz.

Zapoznajmy się najpierw z programem typu key logger:

In [1]:
pip install keyboard

   ---------------------------------------- 0.0/58.1 kB ? eta -:--:--
   ------- -------------------------------- 10.2/58.1 kB ? eta -:--:--
   -------------- ------------------------- 20.5/58.1 kB 320.0 kB/s eta 0:00:01
   --------------------- ------------------ 30.7/58.1 kB 259.2 kB/s eta 0:00:01
   ---------------------------------------- 58.1/58.1 kB 382.9 kB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [1]:
import keyboard


def report_key(event):
    print(event.scan_code)

keyboard.on_release(callback=report_key)
keyboard.wait()

KeyboardEvent(K up)
KeyboardEvent(R up)
KeyboardEvent(Y up)
KeyboardEvent(S up)
KeyboardEvent(T up)
KeyboardEvent(I up)
KeyboardEvent(A up)
KeyboardEvent(N up)


In [2]:
import keyboard


def report_key(event):
    print(event.scan_code)

keyboard.on_release(callback=report_key)
keyboard.wait()

75
77


UWAGA! Aby uruchomić powyższy kod na Linuxie konieczne są uprawnienia administratora (pytanie poza konkursem - dlaczego?)

### Ćwiczenie 1: Wykorzystując powyższy kod napisz keylogger, który zapisuje wszystkie uderzenia w klawisze do pliku. Format pliku jest dowolny, każdy wpis musi zawierać precyzyjną godzinę uderzenia oraz uderzony klawisz. Uruchom program i przepisz paragraf dowolnie wybranego tekstu.

In [50]:
import keyboard
import datetime

def report_key(event):
    with open('pause.txt', 'a') as f:
        timestamp = datetime.datetime.now().strftime('%H:%M:%S')
        f.write(f'{timestamp}\t{event.name}\t{event.scan_code}\n')
    

keyboard.on_release(callback=report_key)
keyboard.wait()

#https://www.netia.pl/pl/blog/co-to-jest-keylogger-i-jak-go-wykryc
# wynik pierwszego paragraphu po drugim nagłówki w pliku keylogger.txt

Celem powyższego ćwiczenia jest pozyskanie danych testowych. Dalsze analizy będziemy prowadzili już bez key loggera, starając się korzystać jedynie z danych zapisanych w pliku. Oczywiście, jeśli zajdzie taka konieczność, można w każdej chwili wygenerować sobie nowy plik.

### Ćwiczenie 2: Napisz program, który wyliczy średnią prędkość pisania. Wykryj, kiedy użytkownik zaczął pisać. Nie bierz pod uwagę przerw dłuższych niż 5 sekund. Podaj prędkość pisania w znakach na minutę oraz słowach na minutę.

In [78]:
from datetime import datetime

def calculate_typing_speed():
    with open('keylogger.txt', 'r') as f:
        start_time = None
        end_time = None
        chars = 0
        words = 0
        
        break_time = 0
        last_time = None

        lines = f.readlines()
        length = len(lines)
        for i in range(length):

            time, key, code = lines[i].strip().split('\t')

            if start_time is None:
                start_time = time
            elif i == length - 1:
                end_time = time

            if code in "42, 54, 541, 75 , 77": #shift, alt, left, right,
                pass
            elif code == '14': #backspace
                chars -= 1
            elif code == '57' or code == '28': #space, enter
                words += 1
            else:
                chars += 1
            
            if last_time:
                s = datetime.strptime(time, "%H:%M:%S")
                e = datetime.strptime(last_time, "%H:%M:%S") 
                time_difference = e - s
                
                if  last_time and time_difference.total_seconds() > 5:
                    break_time += time_difference.total_seconds()
            
            last_time = time
            
    s = datetime.strptime(start_time, "%H:%M:%S")
    e = datetime.strptime(end_time, "%H:%M:%S")
    time_difference = e - s
    seconds = time_difference.total_seconds() - break_time 
  
    chars_per_m = chars / (seconds // 60)  
    words_per_m = words / (seconds // 60)     

    return (seconds,int(chars_per_m), int(words_per_m))

seconds, chars, words = calculate_typing_speed()

print(f'Łączny czas pisania = {int(seconds//60)}:{int(seconds%60)} ')
print(f'Napisano {chars} znaków na minutę')
print(f'Napisano {words} słów na minutę')



Łączny czas pisania = 2:14 
Napisano 256 znaków na minutę
Napisano 37 słów na minutę


Wróćmy teraz do procesu tłumaczenia. Analiza uderzeń klawiszy wykonanych podczas tłumaczenia pozwala wykryć dłuższe pauzy. Pauzy te najczęściej wskazują miejsca, w których tłumacz musi się głębiej zastanowić nad tłumaczeniem danego słowa lub frazy. Przerwę tę wykorzystuje na przykład na sprawdzenie tłumaczenia lub definicji w słowniku, przeglądanie wyników z pamięci tłumaczeń lub korzystanie z innych pomocy (eye-tracking mógłby w tym przypadku rozstrzygnąć, czym w istocie zajmuje się w tym momencie tłuamcz). Jest też możliwe, że tłumacz poświęca pauzę na tzw. cognitive pause-and-unload - rodzaj zamyślenia, pozwalający oczyścić myśli. Z punktu widzenia projektowania systemu wspomagającego tłumaczenie niezwykle istotna jest informacja, nad czym tłumacz musi się dłużej zastanowić. Minimalizacja liczby i czasu trwania takich przerw jest szansą na usprawnienie procesu tłumaczenia.

### Ćwiczenie 3: Napisz program do wykrywania przerw w pisaniu. Raportuj długość oraz miejsce wystąpienia przerwy podając 20-znakowy kontekst z każdej strony. Wykryj każdą przerwę dłuższą niż 3 sekundy, posortuj wyniki malejąco po długości przerwy.

In [5]:
from datetime import datetime

def find_pauses():
    with open('pause.txt', 'r') as f:
        breaks = []
       
        last_time = None
        lines = f.readlines()
        length = len(lines)
        text = ""
        q = 0
        for i in range(length):

            time, key, code = lines[i].strip().split('\t')
            if code in "42, 54, 541, 75 , 77": #shift, alt, left, right,
                q += 1
            elif code == '14': #backspace
                text = text[:-1]
                q += 2
            elif code == '57' or code == '28': #space, enter
                text += " "
            else:
                text += key
            
            
            if last_time:
                s = datetime.strptime(time, "%H:%M:%S")
                e = datetime.strptime(last_time, "%H:%M:%S") 
                time_difference = (s-e).total_seconds()
                
                if  last_time and time_difference > 5:
                    if i-20 >= 0:
                        breaks.append([time_difference, [text[i-q-20:i+1-q],key,""],i-q,i])
                    else:
                        breaks.append([time_difference, [text[:i+1-q],key,""],i-q,i])
            last_time = time
        
    for break_ in breaks:
        i = break_[2]
        if i+20 <= length:
            break_[1][2] = text[i+1:i+20]
        else:
            break_[1][2] = text[i+1:]  
         
    breaks = sorted(breaks, key=lambda x: x[0])
    return breaks


for pause in find_pauses():
    print(f"Pauza: {pause[0]}s Ilość wciśniętych klawiszy do pauzy: {pause[3]} -> text: {pause[1][0]}|{pause[1][1]}|{pause[1][2]}")

Pauza: 6.0s Ilość wciśniętych klawiszy do pauzy: 331 -> text: dzania baza danych (D|H|BMS).  Historia SQL
Pauza: 8.0s Ilość wciśniętych klawiszy do pauzy: 680 -> text: z dnych to korzystani|P|e z SQl-a. Pierwsza
Pauza: 12.0s Ilość wciśniętych klawiszy do pauzy: 341 -> text: za danych (DBMS).  Hi|S|storia SQL zostal o
Pauza: 13.0s Ilość wciśniętych klawiszy do pauzy: 1327 -> text:  SQL: . SQL DML2. SQL|enter| DDL . SQL DCL .tab
Pauza: 15.0s Ilość wciśniętych klawiszy do pauzy: 1147 -> text: zona przez brytyjskďż|S|˝ wytwornIe lotnicz
